# Imports

In [ ]:
# 🏷️ Cell 1: همه‌ی importها
import pandas as pd
import numpy as np
from parsivar import Normalizer, Tokenizer, FindStems
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.decomposition import TruncatedSVD
import matplotlib.pyplot as plt


# Reading Dataset

In [22]:
df = pd.read_csv('persian-news-dataset.csv', delimiter="\t")
documents = df['content'].dropna().tolist()
documents

['حسن جوهرچی بازیگر سینما و تلویزیون ایران در گفتگو با خبرنگار حوزه سینما گروه فرهنگی باشگاه خبرنگاران جوان؛ در خصوص علت کم کاری\u200cاش در چند سال اخیر گفت: با در نظر گرفتن نبود بودجه کافی که در پی آن تولید کم خواهد شد اکثر بازیگران کم کار می\u200cشوند امیدوارم وضعیت بودجه رو به بهبود رود و تولیدات مثل قدیم افزایش یابد تا اینکه حرکت جدیدی اتفاق بیفتد و ما دوباره به طور دائم سرکار باشیم. وی در خصوص حال و هوای این روزهای سینما ایران بیان کرد: به نظر می\u200cرسد که سینما کم\u200cکم در حال تعطیل شدن است، یعنی آثار سینمایی ما مخاطب را جذب نمی\u200cکند، سالن\u200cها خالی و فیلمسازان خوب با کم کاری و یا اصلا فعالیت نمی\u200cکنند که این جای تاسف دارد، امیدوارم مسئولان سینمایی فکری به حال این موضوع به خصوص در بخش تولید و فیلم\u200cنامه داشته باشند تا اینکه سینما به روزهای درخشان خود بازگردد. وی ادامه داد: بحث فیلم\u200cنامه اولین موضوع در تولید و ساختار یک فیلم است و سینمای ما از قدیم\u200cالایام با این جریان مشکل داشته در صورتی که اواخر دهه شصت و اوایل دهه هفتاد آثار خوبی در سینما ساخته می\u2

# Preprocessing

In [23]:
normalizer = Normalizer()
tokenizer = Tokenizer()
stemmer = FindStems()

def preprocess(text):
    text = normalizer.normalize(text)
    tokens = tokenizer.tokenize_words(text)
    stems = [stemmer.convert_to_stem(token) for token in tokens]
    return ' '.join(stems)

preprocessed_documents = [preprocess(doc) for doc in documents]
preprocessed_documents

['حسن جوهر بازیگر سینما و تلویزیون ایران در گفتگو با خبرنگار حوزه سینما گروه فرهنگی باشگاه خبرنگار جوان ؛ در خصوص علت کم کاری\u200cاش در چند سال اخیر گفت : با در نظر گرفتن نبود بودجه کافی که در پی آن تولید کم خواست&خواه شد اکثر بازیگر کم کار شد&شو امیدوار وضعیت بودجه رو به بهبود رود و تولیدات مثل قدیم افزایش یافت&یاب تا اینکه حرکت جدیدی اتفاق افتاد&افت و ما دوباره به\u200cطور دائم سرکار باشیم . وی در خصوص حال و هوا این روزهای سینما ایران بیان کرد : به نظر رسید&رس که سینما کم\u200cکم در حال تعطیل شدن اس ، یعنی اثر سینمایی ما مخاطب را جذب کرد&کن ، سالن خالی و فیلمساز خوب با کم کاری و یا اصلا فعالیت کرد&کن که این جای تاسف داشت&دارد ، امیدوار مسئول سینمایی فکری به حال این موضوع به خصوص در بخش تولید و فیلم\u200cنامه داشته باشند تا اینکه سینما به روزهای درخشان خود بازگردد . وی ادامه داد : بحث فیلم\u200cنامه اولین موضوع در تولید و ساختار یک فیلم اس و سینما ما از قدیم\u200cالایام با این جریان مشکل داشته در صورتی که اواخر دهه شصت و اوایل دهه هفتاد اثر خوبی در سینما ساخته شد&شو اما متاسفانه این 

# Search Implementation using Data Vectorization

In [24]:
def search(query, top_k=5):
    vectorizer = TfidfVectorizer()
    X = vectorizer.fit_transform(preprocessed_documents)
    query = preprocess(query)
    query_vec = vectorizer.transform([query])
    similarities = cosine_similarity(query_vec, X).flatten()
    top_indices = np.argsort(similarities)[::-1][:top_k]
    results = [(documents[idx], similarities[idx]) for idx in top_indices]
    return results

query = "توسعه نرم افزار"
results = search(query)
for doc, score in results:
    print(f"Similarity: {score:.4f} | Document: {doc}")

Similarity: 0.4060 | Document: شرایط احراز برنامه نویس نرم افزار‌های تحت وب مسلط به MVC، C، SQL Server آشنا به مفاهیم Object Oriented، JQuery، Ajax دارای روحیه کار تیمی با حداقل ۲ سال سابقه کار مفید انجام عملیات تولید نرم افزار انجام عملیات تست و عیب یابی آنالیز و طراحی پایگاه داده خلاق در تحلیل نرم افزار با رویکرد حل مساله کارآموز طراح و برنامه نویس ویندوز و وب ترجیحا آشنا به C و SQL Server دارای حداقل مدرک کاردانی رشته‌های مرتبط کارشناس پشتیبان فنی نرم افزار مالی آشنا به C و SQL با حداقل ۲ سال سابقه کار مرتبط ارائه پشتیبانی حضوری و تلفنی انجام عملیات راه اندازی نرم افزار مسئول دفتر یا منشی با حداقل ۲ سال سابقه کار مرتبط و روابط عمومی بالا پاسخگویی به تماس‌های تلفنی، انجام امور دفتری جهت پشتیبانی و استقرار نرم افزار مالی، مسلط به مفاهیم حسابداری با حداقل ۲ سال سابقه کار مرتبط ارائه پشتیبانی حضوری و تلفنی آموزش مشتریان به صورت حضوری و غیر حضوری انجام عملیات استقرار و راه اندازی نرم افزار کارشناس فروش و بازاریابی با روابط عمومی بالا ترجیحا با سابقه فروش نرم افزار دارای مدرک کارشناسی یا 

# Fast Search Implementation using ANNS

In [25]:
svd = TruncatedSVD(n_components=100)
X_reduced = svd.fit_transform(X)

def search_fast(query, top_k=5):
    query = preprocess(query)
    query_vec = vectorizer.transform([query])
    query_vec_reduced = svd.transform(query_vec)
    similarities = cosine_similarity(query_vec_reduced, X_reduced).flatten()
    top_indices = np.argsort(similarities)[::-1][:top_k]
    results = [(documents[idx], similarities[idx]) for idx in top_indices]
    return results

# جستجوی سریع
fast_results = search_fast("برنامه نویسی کامپیوتر")
for doc, score in fast_results:
    print(f"[FAST] Similarity: {score:.4f} | Document: {doc}")

NameError: name 'TruncatedSVD' is not defined